# 1.Load data

In [1]:
import pandas as pd
import imblearn
import numpy as np

In [2]:
data = pd.read_csv('./OUTPUT/dataset.csv', encoding= 'unicode_escape')
data

Sentence          Word  Tag
0            Sentence: 1        RECORD    0
1            Sentence: 2            OC    0
2                    NaN            AM    0
3                    NaN     gallstone    0
4                    NaN  pancreatitis    0
...                  ...           ...  ...
949802               NaN          M.D.    0
949803  Sentence: 132094           END    0
949804               NaN            OF    0
949805               NaN     DISCHARGE    0
949806               NaN        ORDERS    0

[949807 rows x 3 columns]

## Groupby

In [3]:
data_fillna = data.fillna(method='ffill', axis=0)
data_group = data_fillna.groupby(['Sentence'],as_index=False
                                )['Word', 'Tag'].agg(lambda x: list(x))

#data_fillna
data_group

<ipython-input-3-73aff18756c8>:2: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  data_group = data_fillna.groupby(['Sentence'],as_index=False


Sentence                                               Word  \
0           Sentence: 1                                           [RECORD]   
1          Sentence: 10  [WILL, D/C, ORDER, BE, USED, AS, THE, D/C, SUM...   
2         Sentence: 100  [prandial, N/V/severe, upper, abdominal, pain....   
3        Sentence: 1000  [normal, limits., Cardiac, catheterization, da...   
4       Sentence: 10000  [year, old, Black, female, with, significant, ...   
...                 ...                                                ...   
132089  Sentence: 99995  [Height, foot, inch, and, weight, kg., Tempera...   
132090  Sentence: 99996  [degrees, heart, rate, and, sinus, blood, pres...   
132091  Sentence: 99997  [blood, pressure, left, arm, and, oxygen, satu...   
132092  Sentence: 99998  [No, carotid, bruits, regular, rate, and, rhyt...   
132093  Sentence: 99999  [systolic, murmur, along, the, right, upper, s...   

                                   Tag  
0                                  [0]  
1       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]  
2          [0, 1, 0, 1, 1, 0, 0, 0, 0]  
3             [0, 0, 0, 0, 0, 0, 0, 0]  
4       [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]  
...                                ...  
132089           [0, 0, 0, 0, 0, 0, 0]  
132090     [0, 0, 0, 0, 0, 0, 0, 0, 0]  
132091           [0, 0, 0, 0, 0, 0, 0]  
132092     [0, 0, 0, 0, 0, 0, 0, 0, 0]  
132093     [0, 0, 0, 0, 0, 0, 0, 0, 0]  

[132094 rows x 3 columns]

## GLOVE Embedding Layer

In [6]:
texts = data_group['Word'].tolist()  
labels = data_group['Tag'].tolist()  

In [8]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split

tokenizer = Tokenizer()
tokenizer.fit_on_texts(texts)
sequences = tokenizer.texts_to_sequences(texts)

word_index = tokenizer.word_index
print('Found %s unique tokens.' % len(word_index))

pad_tokens = pad_sequences(sequences, maxlen=49, dtype='int32', padding='post', value= 0)
print(pad_tokens)
pad_tags = pad_sequences(labels, maxlen=49, dtype='int32', padding='post', value= 0)
train_tokens, test_tokens, train_tags, test_tags = train_test_split(pad_tokens, pad_tags, test_size=0.2, train_size=0.8, random_state=2020)
print(pad_tags)
print('Shape of data tensor:', pad_tokens.shape)
print('Shape of label tensor:', pad_tags.shape)

Found 34275 unique tokens.
[[  115     0     0 ...     0     0     0]
 [   44   145   106 ...     0     0     0]
 [ 6315 15212   259 ...     0     0     0]
 ...
 [   42    70    33 ...     0     0     0]
 [   13   421  1398 ...     0     0     0]
 [  327   561  1373 ...     0     0     0]]
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 1 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
Shape of data tensor: (132094, 49)
Shape of label tensor: (132094, 49)


In [9]:
index = 0
for token, tag in zip(train_tokens, train_tags):
    if np.sum(tag) >= 1:
        token_arr = np.tile(token, 20).reshape((-1, len(token)))
        tag_arr = np.tile(tag, 20).reshape((-1, len(tag)))
        train_tokens = np.append(token_arr, train_tokens, axis=0)
        train_tags = np.append(tag_arr, train_tags, axis=0)
        print(tag)
        print(token)
        print('index: ' + str(index))
        print('-------------------')
    index = index + 1

[0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[   79    59     7  1156 11229   666   932    44   358     5     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 35
-------------------
[0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[9586   16  741  114   34   30   15   31   67    2   21  522    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 44
-------------------
[0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[931 287 173 138 215 862  15   0   0   0   0   0   0   0   0   0   0   0
   0   0   0  

[0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[3409   12 4600 1727  326 1203    3    1 1376    2    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 214
-------------------
[0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[    2   987    34    30     2 12723     1    11     4   279     6     1
  1298   728     4     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 215
-------------------
[0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  12   23 8294   10    1  306 1652    0    0    0    0    0    0    0
    0    0    

[0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 487  436 1200    2  202 1956    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 509
-------------------
[0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[8613   24   76  787 1629   35  152    3    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 522
-------------------
[0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  675  7862 19647  7490     2     4   101     6    14  1187     0     0
     0     0     0     0     0     0     0     0     0     0  

[0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 821   35   17 6009   46   30    2 6009   46  623    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 724
-------------------
[1 1 1 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[2211   34 1268   27 2006   34  192   12  376   37    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 730
-------------------
[0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[213 243 574   7 269   3 387 213  30   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0  

[0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[259 344 506  34  30   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0]
index: 959
-------------------
[0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  27 1133  844   14  261 1845 2589    4    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 967
-------------------
[0 0 0 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[1861 2475  618   30   13  512    3 2729 1273  179 1603 1861 5514    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0   

...

[10618    12   109    37    48   114   736     7   431     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 104595
-------------------
[0 0 1 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  724     5  1450 31052    16    23  1711  1455  3025    10     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 104608
-------------------
[1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  179     2  9183 13452    14  4043     6    28    32   241     0     0
     0     0     0     0     0     0     0     0     0   

[0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[24221    82  1099   352   560  5790  5136 11446    68   122    28    49
   107    78     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 104792
-------------------
[1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[501   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
   0   0   0   0   0   0   0   0   0   0   0   0   0]
index: 104798
-------------------
[1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[2135   16  109   37 5804  114 2471   16   52  941    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0   

[1 1 0 1 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[    3   149   218  1300    10   451     3   438   285 27753     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 105017
-------------------
[0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  233  1213  2152  2915 11507   103   616 24998   805  3790     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 105018
-------------------
[0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 3630    35    30  3348   27

[0 0 1 1 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 253    3 1539 1140 1006  730  912 3616  702   52   25 4840    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 105241
-------------------
[1 0 0 1 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 179    2  438  213 2423   12  345  114   34    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 105299
-------------------
[1 0 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[ 5916     2  2560  1460 12596   702  3041 17854    16    23    57   584
   467     0     0     0     0     0     0     0     0  

[0 1 0 1 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[  13  644   13 7230  147   86 3794   10  427  912    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0]
index: 105516
-------------------
[0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[22665  3887    13 11250  4372    12   345   722  1376     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0]
index: 105518
-------------------
[0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0]
[3355  510   99 1895    1   11   52  137   31   14    0    0    0    0
    0   

In [10]:
import os

embeddings_index = {}
f = open(os.path.join(r'./GLOVE', 'glove.6B.300d.txt'), encoding="utf8")
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()

print('Found %s word vectors.' % len(embeddings_index))

Found 400000 word vectors.


In [11]:
embedding_matrix = np.zeros((len(word_index) + 1, 300))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector

In [12]:
from keras.layers import Embedding

embedding_layer = Embedding(len(word_index) + 1,
                            300,
                            weights=[embedding_matrix],
                            input_length=49,
                            trainable=True)

## Model

In [13]:
import numpy as np
import tensorflow as tf
from tensorflow.keras import Sequential, Model, Input
from tensorflow.keras.layers import LSTM, Embedding, Dense, TimeDistributed, Dropout, Bidirectional
from tensorflow.keras.utils import plot_model
from keras import backend as K
import keras as keras
from keras.datasets import mnist
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from sklearn.metrics import roc_auc_score
from keras import metrics
from sklearn.utils import class_weight

In [14]:
def recall_m(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    recall = true_positives / (possible_positives + K.epsilon())
    return recall

def precision_m(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision = true_positives / (predicted_positives + K.epsilon())
    return precision

def f1_m(y_true, y_pred):
    precision = precision_m(y_true, y_pred)
    recall = recall_m(y_true, y_pred)
    return 2*((precision*recall)/(precision+recall+K.epsilon()))

In [17]:
def get_bilstm_lstm_model():
    model = Sequential()

    # Add Embedding layer
    model.add(embedding_layer)
    # Add bidirectional LSTM
    model.add(Bidirectional(LSTM(units=32, return_sequences=True, dropout=0.2, recurrent_dropout=0.2), merge_mode = 'concat'))

    
    # Add LSTM
    model.add(LSTM(units=32, return_sequences=True, dropout=0.5, recurrent_dropout=0.5))

    # Add timeDistributed Layer
    model.add(TimeDistributed(Dense(1, activation="sigmoid")))
    
    #Optimiser 
    adam = tf.keras.optimizers.Adam(learning_rate=0.0005, beta_1=0.9, beta_2=0.999)
    
    # Compile model
    model.compile(loss='binary_crossentropy', sample_weight_mode="temporal", optimizer='adam', metrics=['acc', precision_m, recall_m, f1_m])
    model.summary()
    
    return model

In [18]:
model = get_bilstm_lstm_model()
    
#Running Model
history = model.fit(train_tokens, train_tags, batch_size=128, verbose=1, epochs=20, validation_split = 0.2)

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 49, 300)           10282800  
                                                                 
 bidirectional_1 (Bidirectio  (None, 49, 64)           85248     
 nal)                                                            
                                                                 
 lstm_2 (LSTM)               (None, 49, 32)            12416     
                                                                 
 time_distributed (TimeDistr  (None, 49, 1)            33        
 ibuted)                                                         
                                                                 
Total params: 10,380,497
Trainable params: 10,380,497
Non-trainable params: 0
_________________________________________________________________
Epoch 1/20
 246/1795 [===>................

KeyboardInterrupt: 

In [74]:
model.evaluate(test_tokens, test_tags)

826/826 [==============================] - 17s 20ms/step - loss: 0.0056 - acc: 0.9983 - precision_m: 0.7332 - recall_m: 0.6684 - f1_m: 0.6718


[0.005551586858928204,
 0.9983221292495728,
 0.7331998944282532,
 0.6684271097183228,
 0.6718094348907471]